In [1]:
import pandas as pd 
import requests
import os
import json
import numpy as np

In [3]:
#import nhl_data
nhl_data = pd.read_csv(r'C:\Users\akobe\OneDrive\Desktop\Lighthouse\After\Predicting_Success_all_Rounds_NHL\Data\nhl_data_all_rounds.csv', index_col = [0]) #index col makes sures another index column is not needed

In [4]:
with open(r'C:\Users\akobe\OneDrive\Documents\Keys\eliteKey.txt') as content:
    elite_key = content.read()

In [5]:
nhl_data.head(2)

draft_year  draft_round  pick_no                 team  prospect_name  \
0        2009            1        1   New York Islanders   John Tavares   
1        2009            1        2  Tampa Bay Lightning  Victor Hedman   

   prospect_id         dob birth_country height  weight shoots   nhl_id  \
0        24111  1990-09-20           CAN  6' 1"     209      L  8475166   
1        33799  1990-12-18           SWE  6' 6"     220      L  8475167   

  position      prospect_category amateur_league amateur_team  \
0        C  North American Skater            OHL       London   
1        D        European Skater         SWEDEN         Modo   

   nhl_games_played  200+games  
0              1029          1  
1               974          1

In [12]:
nhl_data.isnull().sum()

draft_year           0
draft_round          0
pick_no              0
team                 0
prospect_name        0
prospect_id          0
dob                  0
birth_country        0
height               0
weight               0
shoots               0
nhl_id               0
position             0
prospect_category    0
amateur_league       0
amateur_team         0
nhl_games_played     0
200+games            0
dtype: int64

In [9]:
#the columns that have missing values 
cols_missing_vals = ['birth_country', 'height', 'shoots', 'position']

In [10]:
#replacing the missing values 
nhl_data[cols_missing_vals] = nhl_data[cols_missing_vals].replace(0, np.NaN) # replace 0's with NaNs

In [11]:
#drop rows with NaN's 
nhl_data = nhl_data.dropna(subset=['birth_country', 'height', 'shoots', 'position'])

In [7]:
#update to the correct dob 
#nhl_data.at[11, 'dob'] = '1991-05-09'

In [13]:
#nhl_data.to_csv('NaNs_removed.csv')

In [149]:
len(nhl_data)

1867

In [14]:
nhl_data['player_fname'] = nhl_data['prospect_name'].apply(lambda x: x[0:x.find(" ")])

In [15]:
nhl_data['player_lname'] = nhl_data["prospect_name"].apply(lambda x: x[x.find(" ")+1:])

In [16]:
#creates a list of the NHL id's so we can add it to the dataframe to easily join the dataframes afterwards 
nhl_id = []
nhl_id = nhl_data['nhl_id'].tolist()

In [17]:
draft_year = []
draft_year = nhl_data['draft_year'].tolist()

In [20]:
#create a list of player names - for API call 
player_fname = []
player_lname = []
dob = []

player_fname = nhl_data['player_fname'].tolist()
player_lname = nhl_data['player_lname'].tolist()
dob =  nhl_data['dob'].tolist()

In [90]:
#name updated so that can pull API
player_lname[11] = 'De%20Haan'
player_lname[472] = 'St.%20Croix'
player_lname[598] = 'Di%20Giuseppe'
player_lname[652] = 'Di%20Pauli'
player_lname[711] = 'De%20Haas'
player_lname[777] = 'De%20La%20Rose'
player_lname[863] = 'Crus%20Rydberg'
player_lname[916] = 'De%20Jong'
player_lname[932] = 'Dal%20Colle'
player_lname[1017] = 'De%20Leo'
player_lname[1082] = 'Ollas%20Mattsson'
player_lname[1130] = 'Eriksson%20Ek'
player_lname[1153] = 'Forsbacka%20Karlsson'
player_lname[1184] = 'Gates%20Jr.'
player_lname[1186] = 'Vande%20Sompel'
player_lname[1395] = 'Haman%20Aktell'
player_lname[1485] = 'Krag%20Christensen'
player_lname[1636] = 'De%20Jong'
player_lname[1658] = 'Walli%20Walterholm'
player_lname[1679] = 'Roykas%20Marthinsen'
player_lname[1786] = 'St.%20Ivany'
player_lname[1790] = 'Lindstrand%20Cronholm'
player_lname[1830] = 'Emilio%20Pettersen'
player_lname[1834] = 'Worge%20Kreu'

In [39]:
#update to proper dob
dob[11] = '1991-05-09'

In [89]:
player_lname[1830]

'Emilio Pettersen'

In [91]:
#getting all the url's to pull the data from elite prospects 
all_elite_url = []
for i in range(1867):
    first_name = player_fname[i]
    last_name = player_lname[i]
    birth_date = dob[i]
    elite_url = 'https://api.eliteprospects.com/v1/players?offset=0&limit=1000&sort=name&name='+first_name+'%20'+last_name+'&dateOfBirth='+str(birth_date)+'&apiKey='
    all_elite_url.append(elite_url)

In [130]:
all_elite_url

['https://api.eliteprospects.com/v1/players?offset=0&limit=1000&sort=name&name=John%20Tavares&dateOfBirth=1990-09-20&apiKey=',
 'https://api.eliteprospects.com/v1/players?offset=0&limit=1000&sort=name&name=Victor%20Hedman&dateOfBirth=1990-12-18&apiKey=',
 'https://api.eliteprospects.com/v1/players?offset=0&limit=1000&sort=name&name=Matt%20Duchene&dateOfBirth=1991-01-16&apiKey=',
 'https://api.eliteprospects.com/v1/players?offset=0&limit=1000&sort=name&name=Evander%20Kane&dateOfBirth=1991-08-02&apiKey=',
 'https://api.eliteprospects.com/v1/players?offset=0&limit=1000&sort=name&name=Brayden%20Schenn&dateOfBirth=1991-08-22&apiKey=',
 'https://api.eliteprospects.com/v1/players?offset=0&limit=1000&sort=name&name=Oliver%20Ekman-Larsson&dateOfBirth=1991-07-17&apiKey=',
 'https://api.eliteprospects.com/v1/players?offset=0&limit=1000&sort=name&name=Nazem%20Kadri&dateOfBirth=1990-10-06&apiKey=',
 'https://api.eliteprospects.com/v1/players?offset=0&limit=1000&sort=name&name=Scott%20Glennie&dateOf

In [93]:
len(all_elite_url)

1855

In [131]:
all_elite_url_1 = all_elite_url[0:500]
all_elite_url_2 = all_elite_url[501:1000]
all_elite_url_3 = all_elite_url[1001:1500]
all_elite_url_4 = all_elite_url[1501:]

#### split into 4 as errorred out when trying to pull everything at once 

In [132]:
elite_data= []

In [133]:
#get request for all url's 
for j in range(len(all_elite_url_1)):
    response = requests.get(all_elite_url_1[j]+elite_key)
    elite_data.append(response.json())

In [134]:
#get request for url's 501-1000
for j in range(len(all_elite_url_2)):
    response = requests.get(all_elite_url_2[j]+elite_key)
    elite_data.append(response.json())

In [103]:
elite_data2 = []

In [135]:
#get request for all url's 1001-1500
for j in range(len(all_elite_url_3)):
    response = requests.get(all_elite_url_3[j]+elite_key)
    elite_data.append(response.json())

In [136]:
#get request for all url's 1501-end
for j in range(len(all_elite_url_4)):
    response = requests.get(all_elite_url_4[j]+elite_key)
    elite_data.append(response.json())

In [137]:
from IPython.display import JSON
JSON(elite_data)

<IPython.core.display.JSON object>

In [144]:
#creating empty lists 
elite_id = []
elite_name = []

In [145]:
for i in range(len(elite_data)):
    if len(elite_data[i]['data']) > 0:
        elite_id.append(elite_data[i]['data'][0]['id'])
        elite_name.append(elite_data[i]['data'][0]['name'])
    else:
        #if there is no value replace with NAN
        elite_id.append('NaN')
        elite_name.append('NaN')  

In [146]:
#create a data frame with the information 
elite_data_df = pd.DataFrame(list(zip(elite_id, elite_name)),
               columns =['elite_id', 'elite_name'])

In [147]:
len(elite_data_df)

1852

In [148]:
#elite_data_df.to_csv('elite_data_df_1852.csv')

In [97]:
#find NaN's 
elite_data.isnull().sum()

nhl_id        0
elite_id      0
elite_name    0
elite_dob     0
dtype: int64

In [151]:
elite_data_only = pd.read_csv(r'C:\Users\akobe\lighthouse-data-notes\Data\elite_data_df_1852.csv', index_col = [0],  encoding='latin-1') 

In [153]:
elite_data_only['nhl_id'] = nhl_id

In [154]:
elite_data_only.head()

elite_id      elite_name   nhl_id
0.0    9223.0    John Tavares  8475166
1.0    6007.0   Victor Hedman  8475167
2.0   12571.0    Matt Duchene  8475168
3.0   14657.0    Evander Kane  8475169
4.0   14739.0  Brayden Schenn  8475170

In [155]:
#save the data to csv -
elite_data_only.to_csv('info_for_pulling_prospects.csv')

In [157]:
elite_data = elite_data_only

# draft year data 

In [161]:
elite_data['draft_year'] = draft_year

In [162]:
#draft season is the year before and year of draft
#this information is needed for the API call to only get stats for their draft year 
draft_season = []

for i in elite_data['draft_year']: 
    if i == 2009:
        draft_season.append('2008-2009')
    elif i == 2010:
        draft_season.append('2009-2010')
    elif i == 2011:
        draft_season.append('2010-2011')
    elif i == 2012:
        draft_season.append('2011-2012')
    elif i == 2013:
        draft_season.append('2012-2013')
    elif i == 2014:
        draft_season.append('2013-2014')
    elif i == 2015:
        draft_season.append('2014-2015')
    elif i == 2016:
        draft_season.append('2015-2016')
    elif i == 2017:
        draft_season.append('2016-2017')
    elif i == 2018:
        draft_season.append('2017-2018')

In [163]:
#add the list to the dataframe 
elite_data['draft_season'] = draft_season

In [164]:
elite_id = []
draft_season = []

elite_id = elite_data['elite_id'].tolist()
draft_season = elite_data['draft_season'].tolist()

## Pull Prospect stats

In [45]:
#### START FROM HERE 
elite_data = pd.read_csv(r'C:\Users\akobe\lighthouse-data-notes\Data\info_for_pulling_prospects.csv', index_col = [0]) #index col makes sures another index column is not needed

In [165]:
#urls for draft year stats 
all_elite_prospect_url = []
for i in range(len(elite_data)):
    ident = elite_id[i]
    season = draft_season[i]
    elite_prospect_url = 'https://api.eliteprospects.com/v1/players/'+str(ident)+'/stats?offset=0&limit=100&sort=season&season='+season+'&team.teamType=club&apiKey='
    all_elite_prospect_url.append(elite_prospect_url)

In [166]:
len(all_elite_prospect_url)

1867

In [167]:
#need to split up to pull properly 
all_elite_url_5 = all_elite_prospect_url[0:500]
all_elite_url_6 = all_elite_prospect_url[500:1000]
all_elite_url_7 = all_elite_prospect_url[1000:1500]
all_elite_url_8 = all_elite_prospect_url[1500:]

In [168]:
elite_prospect_data = []
#0-499

for j in range(len(all_elite_url_5)):
    response = requests.get(all_elite_url_5[j]+elite_key)
    elite_prospect_data.append(response.json())

In [170]:
#500-999
for j in range(len(all_elite_url_6)):
    response = requests.get(all_elite_url_6[j]+elite_key)
    elite_prospect_data.append(response.json())

ConnectionError: ('Connection aborted.', ConnectionResetError(10054, 'An existing connection was forcibly closed by the remote host', None, 10054, None))

In [ ]:
#1000-1499
for j in range(len(all_elite_url_7)):
    response = requests.get(all_elite_url_7[j]+elite_key)
    elite_prospect_data.append(response.json())

In [ ]:
#1500-end
for j in range(len(all_elite_url_8)):
    response = requests.get(all_elite_url_8[j]+elite_key)
    elite_prospect_data.append(response.json())

In [52]:
from IPython.display import JSON
JSON(elite_prospect_data)

<IPython.core.display.JSON object>

In [54]:
#replaces null values with 0's 
elite_prospect_data_no_null = json.loads(json.dumps(elite_prospect_data).replace('null', '0'))

In [55]:
JSON(elite_prospect_data_no_null)

<IPython.core.display.JSON object>

In [56]:
#creating empty lists for the data 
prospect_gp = []
prospect_g = []
prospect_a = []
prospect_pts = []
prospect_pim = []
prospect_pm = []

In [57]:
# creates lists of all variables wanted, if a player was with more than one team in their draft year their stats are added together 
##this one mostly works

for prospect in elite_prospect_data_no_null[:]:
    gp = 0
    goals = 0
    assists = 0
    pts = 0
    pim = 0
    pm = 0
    
    prospect_data = prospect['data']
    i = 0
    for prospect_stats in prospect_data:
        #some players were with more than one team in their draft year, this goes through each team and adds the data together 
        i+=1
        if prospect_stats['regularStats'] == 0:   #if there is no info at regularStats, this spasses it and moves onto the next 
            pass
        else:   
            gp += prospect_stats['regularStats']['GP'] 
            goals += prospect_stats['regularStats']['G']
            assists += prospect_stats['regularStats']['A']
            pts += prospect_stats['regularStats']['PTS']
            pim += prospect_stats['regularStats']['PIM']
            pm +=  prospect_stats['regularStats']['PM']

    #appends the information to a new list         
    prospect_gp.append(gp)  
    prospect_g.append(goals)  
    prospect_a.append(assists)  
    prospect_pts.append(pts)  
    prospect_pim.append(pim)  
    prospect_pm.append(pm)  

In [58]:
#create a data frame with the information 
prospect_data = pd.DataFrame(list(zip(elite_id, prospect_gp, prospect_g, prospect_a, prospect_pts, prospect_pim, prospect_pm)),
               columns =['elite_id', 'prospect_gp', 'prospect_g', 'prospect_a', 'prospect_pts', 'prospect_pim', 'prospect_pm'])              

In [157]:
#save the data to csv 
#prospect_data.to_csv('prospect_data.csv')

## Joining elite dataframe 

In [60]:
#joining tables 
all_elite_prospect_data = pd.merge(elite_data, prospect_data,  on = 'elite_id')
all_elite_prospect_data.head()

nhl_id elite_id      elite_name   elite_dob  draft_year draft_season  \
0  8475166     9223    John Tavares  1990-09-20        2009    2008-2009   
1  8475167     6007   Victor Hedman  1990-12-18        2009    2008-2009   
2  8475168    12571    Matt Duchene  1991-01-16        2009    2008-2009   
3  8475169    14657    Evander Kane  1991-08-02        2009    2008-2009   
4  8475170    14739  Brayden Schenn  1991-08-22        2009    2008-2009   

   prospect_gp  prospect_g  prospect_a  prospect_pts  prospect_pim  \
0           56          58          46           104            54   
1           45           7          16            23            62   
2           57          31          48            79            42   
3           61          48          48            96            89   
4           70          32          56            88            82   

   prospect_pm  
0           10  
1           21  
2           32  
3           51  
4           20

In [161]:
#save the data to csv 
#all_elite_prospect_data.to_csv('all_elite_prospect_data.csv')